# Mapping migration

Introduction to vector data operations

## STEP 0: Set up

To get started on this notebook, you’ll need to restore any variables
from previous notebooks to your workspace. To save time and memory, make
sure to specify which variables you want to load.

In [12]:
# Restore variables and import new library
%store -r occurrence_df gbif_eco_gdf eco_gdf

from pathlib import Path

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It: Import packages</div></div><div class="callout-body-container callout-body"><p>In the imports cell, we’ve included some packages that you will need.
Add imports for packages that will help you:</p>
<ol type="1">
<li>Make interactive maps with vector data</li>
<li>Access pre-defined month names</li>
<li>Define Coordinate Reference Systems (CRSs)</li>
</ol></div></div>

In [13]:
# Get month names
import calendar

# Libraries for Dynamic mapping
import cartopy.crs as ccrs
import panel as pn
import hvplot.pandas

### Create a simplified `GeoDataFrame` for plotting

Plotting larger files can be time consuming. The code below will
streamline plotting with `hvplot` by simplifying the geometry,
projecting it to a Mercator projection that is compatible with
`geoviews`, and cropping off areas in the Arctic.

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It: Simplify ecoregion data</div></div><div class="callout-body-container callout-body"><p>Download and save ecoregion boundaries from the EPA:</p>
<ol type="1">
<li>Simplify the ecoregions with <code>.simplify(.05)</code>, and save
it back to the <code>geometry</code> column.</li>
<li>Change the Coordinate Reference System (CRS) to Mercator with
<code>.to_crs(ccrs.Mercator())</code></li>
<li>Use the plotting code that is already in the cell to check that the
plotting runs quickly (less than a minute) and looks the way you want,
making sure to change <code>gdf</code> to YOUR <code>GeoDataFrame</code>
name.</li>
</ol></div></div>

In [14]:
# Simplify the geometry to speed up processing
eco_gdf.geometry = eco_gdf.simplify(
    .05, preserve_topology = False)

# Change the CRS to Mercator for mapping
eco_gdf = eco_gdf.to_crs(ccrs.Mercator())

# Check that the plot runs in a reasonable amount of time
eco_gdf.hvplot(geo=True, crs=ccrs.Mercator())

:Polygons   [Longitude,Latitude]

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It: Map migration over time</div></div><div class="callout-body-container callout-body"><ol type="1">
<li>If applicable, replace any variable names with the names you defined
previously.</li>
<li>Replace <code>column_name_used_for_ecoregion_color</code> and
<code>column_name_used_for_slider</code> with the column names you wish
to use.</li>
<li>Customize your plot with your choice of title, tile source, color
map, and size.</li>
</ol>
<div data-__quarto_custom="true" data-__quarto_custom_type="Callout"
data-__quarto_custom_context="Block" data-__quarto_custom_id="3">
<div data-__quarto_custom_scaffold="true">

</div>
<div data-__quarto_custom_scaffold="true">
<p>Your plot will probably still change months very slowly in your
Jupyter notebook, because it calculates each month’s plot as needed.
Open up the saved HTML file to see faster performance!</p>
</div>
</div></div></div>

In [15]:
occurrence_df.head()

occurrences  norm_occurrences
ecoregion month                               
13.0      5                2          0.000816
          6                2          0.000918
          7                2          0.001760
17.0      4                2          0.000010
          5             3023          0.001701

In [16]:
eco_gdf.head()

OBJECTID                                           ECO_NAME  BIOME_NUM  \
0       1.0                                 Adelie Land tundra       11.0   
1       2.0             Admiralty Islands lowland rain forests        1.0   
2       3.0  Aegean and Western Turkey sclerophyllous and m...       12.0   
3       4.0                       Afghan Mountains semi-desert       13.0   
4       5.0                   Ahklun and Kilbuck Upland Tundra       11.0   

                                       BIOME_NAME        REALM ECO_BIOME_  \
0                                          Tundra   Antarctica       AN11   
1  Tropical & Subtropical Moist Broadleaf Forests  Australasia       AU01   
2        Mediterranean Forests, Woodlands & Scrub   Palearctic       PA12   
3                      Deserts & Xeric Shrublands   Palearctic       PA13   
4                                          Tundra     Nearctic       NE11   

   NNH  ECO_ID  SHAPE_LENG  SHAPE_AREA                           NNH_NAME  \
0    1     117    9.749780    0.038948                     Half Protected   
1    2     135    4.800349    0.170599  Nature Could Reach Half Protected   
2    4     785  162.523044   13.844952                   Nature Imperiled   
3    4     807   15.084037    1.355536                   Nature Imperiled   
4    1     404   22.590087    8.196573                     Half Protected   

     COLOR COLOR_BIO COLOR_NNH    LICENSE  \
0  #63CFAB   #9ED7C2   #257339  CC-BY 4.0   
1  #70A800   #38A700   #7BC141  CC-BY 4.0   
2  #FF7F7C   #FE0000   #EE1E23  CC-BY 4.0   
3  #FA774D   #CC6767   #EE1E23  CC-BY 4.0   
4  #4C82B6   #9ED7C2   #257339  CC-BY 4.0   

                                            geometry  
0  POLYGON ((17090104.083 -10646152.188, 17100906...  
1  MULTIPOLYGON (((16461836.873 -254248.259, 1644...  
2  MULTIPOLYGON (((3391149.749 4336064.109, 33985...  
3  MULTIPOLYGON (((7369001.698 4093509.259, 73168...  
4  MULTIPOLYGON (((-17912546.29 8050475.591, -179...

In [17]:
# Line up column names
eco_gdf = eco_gdf.rename(columns= {"OBJECTID": "ecoregion"})

# Set index to ecoregion
eco_gdf = eco_gdf.set_index('ecoregion')

eco_gdf

ECO_NAME  BIOME_NUM  \
ecoregion                                                                 
1.0                                       Adelie Land tundra       11.0   
2.0                   Admiralty Islands lowland rain forests        1.0   
3.0        Aegean and Western Turkey sclerophyllous and m...       12.0   
4.0                             Afghan Mountains semi-desert       13.0   
5.0                         Ahklun and Kilbuck Upland Tundra       11.0   
...                                                      ...        ...   
848.0                          Sulawesi lowland rain forests        1.0   
212.0                           East African montane forests        1.0   
224.0                                    Eastern Arc forests        1.0   
79.0                             Borneo montane rain forests        1.0   
376.0                        Kinabalu montane alpine meadows       10.0   

                                               BIOME_NAME        REALM  \
ecoregion                                                                
1.0                                                Tundra   Antarctica   
2.0        Tropical & Subtropical Moist Broadleaf Forests  Australasia   
3.0              Mediterranean Forests, Woodlands & Scrub   Palearctic   
4.0                            Deserts & Xeric Shrublands   Palearctic   
5.0                                                Tundra     Nearctic   
...                                                   ...          ...   
848.0      Tropical & Subtropical Moist Broadleaf Forests  Australasia   
212.0      Tropical & Subtropical Moist Broadleaf Forests   Afrotropic   
224.0      Tropical & Subtropical Moist Broadleaf Forests   Afrotropic   
79.0       Tropical & Subtropical Moist Broadleaf Forests  Indomalayan   
376.0                     Montane Grasslands & Shrublands  Indomalayan   

          ECO_BIOME_  NNH  ECO_ID  SHAPE_LENG  SHAPE_AREA  \
ecoregion                                                   
1.0             AN11    1     117    9.749780    0.038948   
2.0             AU01    2     135    4.800349    0.170599   
3.0             PA12    4     785  162.523044   13.844952   
4.0             PA13    4     807   15.084037    1.355536   
5.0             NE11    1     404   22.590087    8.196573   
...              ...  ...     ...         ...         ...   
848.0           AU01    2     156  150.744361    9.422097   
212.0           AF01    3       8  157.848926    5.010930   
224.0           AF01    3       9   34.153333    0.890325   
79.0            IN01    2     220   38.280990    9.358407   
376.0           IN10    3     313    5.722539    0.352694   

                                    NNH_NAME    COLOR COLOR_BIO COLOR_NNH  \
ecoregion                                                                   
1.0                           Half Protected  #63CFAB   #9ED7C2   #257339   
2.0        Nature Could Reach Half Protected  #70A800   #38A700   #7BC141   
3.0                         Nature Imperiled  #FF7F7C   #FE0000   #EE1E23   
4.0                         Nature Imperiled  #FA774D   #CC6767   #EE1E23   
5.0                           Half Protected  #4C82B6   #9ED7C2   #257339   
...                                      ...      ...       ...       ...   
848.0      Nature Could Reach Half Protected  #70A800   #38A700   #7BC141   
212.0                   Nature Could Recover  #13ED00   #38A700   #F9A91B   
224.0                   Nature Could Recover  #267400   #38A700   #F9A91B   
79.0       Nature Could Reach Half Protected  #23DB01   #38A700   #7BC141   
376.0                   Nature Could Recover  #C48832   #D6C39D   #F9A91B   

             LICENSE                                           geometry  
ecoregion                                                                
1.0        CC-BY 4.0  POLYGON ((17090104.083 -10646152.188, 17100906...  
2.0        CC-BY 4.0  MULTIPOLYGON (((16461836.873 -254248.259, 1644...  
3.0        CC-BY 4.0 

In [18]:
# Join the occurrences with the plotting GeoDataFrame
occurrence_gdf = eco_gdf.join(occurrence_df)

In [19]:
# There is an issue with a particular ecoregion (115) that has geometry
# 'MULTIPOLYGON EMPTY' in November that messes with the plot
eco115 = occurrence_gdf[occurrence_gdf.index.get_level_values('ecoregion') == 115]

eco115

ECO_NAME  BIOME_NUM  \
ecoregion month                                                                 
115.0     11     Cayos Miskitos-San Andrés and Providencia mois...        1.0   

                                                     BIOME_NAME      REALM  \
ecoregion month                                                              
115.0     11     Tropical & Subtropical Moist Broadleaf Forests  Neotropic   

                ECO_BIOME_  NNH  ECO_ID  SHAPE_LENG  SHAPE_AREA  \
ecoregion month                                                   
115.0     11          NO01    1     449    0.797686    0.007914   

                       NNH_NAME    COLOR COLOR_BIO COLOR_NNH    LICENSE  \
ecoregion month                                                           
115.0     11     Half Protected  #267400   #38A700   #257339  CC-BY 4.0   

                           geometry  occurrences  norm_occurrences  
ecoregion month                                                     
115.0     11     MULTIPOLYGON EMPTY            2          0.146341

In [20]:
# Remove the ecoregion 115 observation from the new gdf
clean_occ_gdf = occurrence_gdf.drop(115)

# Confirm the ecoregion has been removed
val115 = clean_occ_gdf[clean_occ_gdf.index.get_level_values('ecoregion') == 115]

val115

Empty GeoDataFrame
Columns: [ECO_NAME, BIOME_NUM, BIOME_NAME, REALM, ECO_BIOME_, NNH, ECO_ID, SHAPE_LENG, SHAPE_AREA, NNH_NAME, COLOR, COLOR_BIO, COLOR_NNH, LICENSE, geometry, occurrences, norm_occurrences]
Index: []

In [42]:
# Get the plot bounds so they don't change with the slider
xmin, ymin, xmax, ymax = clean_occ_gdf.total_bounds

# Define Slider
slider = pn.widgets.DiscreteSlider(
    name='month', 
    options={calendar.month_name[i]: i for i in range (1,13)}
)

# Plot occurrence by ecoregion and month
migration_plot = (
    clean_occ_gdf
    .hvplot(
        color = 'norm_occurrences',
        #cmap='Viridis',
        clim = (0,1),
        groupby = 'month',
        # Use background tiles
        geo=True, crs=ccrs.Mercator(), tiles='CartoLight',
        title="Veery Annual Migration",
        xlim=(xmin, xmax), ylim=(ymin, ymax),
        frame_height=600,
        widget_location='bottom',
        widgets = {'month': slider}
        )
    )

migration_plot

BokehModel(combine_events=True, render_bundle={'docs_json': {'06ee735f-f0a7-4ba7-91ab-8b19cf6a4a95': {'version…

In [22]:
# Save the plot if needed
# migration_plot.save('migration.html', 
                        #embed=True, 
                        #backend = 'bokeh')

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-extra"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Looking for an Extra Challenge?: Fix the month labels</div></div><div class="callout-body-container callout-body"><p>Notice that the <code>month</code> slider displays numbers instead of
the month name. Use <code>pn.widgets.DiscreteSlider()</code> with the
<code>options=</code> parameter set to give the months names. You might
want to try asking ChatGPT how to do this, or look at the documentation
for <code>pn.widgets.DiscreteSlider()</code>. This is pretty tricky!</p></div></div>